In [3]:
#!pip install tqdm


[notice] A new release of pip is available: 23.3.1 -> 23.3.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [1]:
from bs4 import BeautifulSoup
import pandas as pd
import configparser 
import requests
from tqdm import tqdm
import warnings
# from snowflake.snowpark import Session
# warnings.filterwarnings('ignore')
import datetime
import re

In [2]:
path = r'D:\project\dataset'

## Snowflake Extract

In [3]:
# config = configparser.ConfigParser()
# config.read(r'C:\Users\stanl\OneDrive\Desktop\Argmarket Project\connections.ini')
date =  datetime.date.today().isoformat()

In [4]:
def Agmarknet_Extraction(DateFrom : datetime, DateTo: datetime, path: str ):
    '''
    Extraction process Built for 'https://agmarknet.gov.in' 
    DateFrom : Date Lower Limit to Extract Data
    DateTo : Date Upper Limit to Extract Data 
    path : Path in Local Directory to Store Local Backup Files
    '''
    try:
        # ACCOUNT = config.get('Extractor_account','account')
        # USER = config.get('Extractor_account','user')
        # PASSWORD = config.get('Extractor_account','password')
        # ROLE = config.get('Extractor_account','role')
        # WAREHOUSE = config.get('Extractor_account','warehouse')
        # DATABASE = config.get('Extractor_account','database')
        # SCHEMA = config.get('Extractor_account','schema')
        # TABLE_NAME = config.get('Table_name_Upload','Table_name')
        # METADATA_TABLE_NAME = config.get('Table_name_Upload','metadata_Table_name')
        # CONNECTION_PARAMETERS = {
        #         "account" : ACCOUNT,
        #         "user" : USER,
        #         "password" : PASSWORD,
        #         "role" : ROLE,  
        #         "warehouse": WAREHOUSE,  
        #         "database" : DATABASE,
        #         "schema" : SCHEMA
        #     }
        # path = config.get('path','project_path')
        # session = Session.builder.configs(CONNECTION_PARAMETERS).create()
        Data_Extract_frames = []
        url = 'https://agmarknet.gov.in'
        request = requests.get(url,timeout=30)
        if request.status_code == 200:
            soup = BeautifulSoup(request.text,'html.parser')
            Commodity = [str(x) for x in soup.find(id="ddlCommodity").find_all('option')]
            States = [str(x) for x in soup.find(id="ddlState").find_all('option')]
            Commodity = [x.replace("<option",'').replace("</option>",'').replace('value=','').replace('"','').strip() for x in Commodity]
            Commodity_dict = {}
            for value in Commodity[1:]:
                value = value.split('>')
                Commodity_dict[value[0]]=value[1].replace(' ','').replace('(','').replace(')','').replace(',','').replace('/','')
            States = [x.replace("<option",'').replace("</option>",'').replace('value=','').replace('"','').strip() for x in States]
            States_dict = {}
            for value in States[1:]:
                value = value.split('>')
                States_dict[value[0]]=value[1]
            commodity_count = []
            try:
                for key_commodity in tqdm(Commodity_dict.keys()):
                    try:
                        
                        parameters = {'Tx_Commodity' : key_commodity,
                        'Tx_State' : '0',
                        'Tx_District' : '0',
                        'Tx_Market' : '0',
                        'DateFrom' : DateFrom,
                        'DateTo' : DateTo,
                        'Fr_Date' : DateFrom,
                        'To_Date' : DateTo,
                        'Tx_Trend' : '2',
                        'Tx_CommodityHead' : Commodity_dict[key_commodity],
                        'Tx_StateHead' : '--Select--',
                        'Tx_DistrictHead' : '--Select--',
                        'Tx_MarketHead' : '--Select--'}
                        request_search = requests.get(url+'/SearchCmmMkt.aspx',params=parameters,timeout=30)
                        soup = BeautifulSoup(request_search.text,'html.parser')
                        column_names = []
                        for th_tags in soup.find_all('th'):
                            b_tags = th_tags.find('b')
                            column_names.append(str(b_tags.text).replace('<b>',''))
                        column_names = ['Commodity']+column_names
                        tr = soup.find_all('tr')[1:]
                        text = []
                        Extracted_text = []
                        
                        for tr_tags in tr:
                            for td_tags in tr_tags.find_all('td'):
                                text.append(td_tags.text)
                            if len(text) < 10:
                                Extracted_text.append([Commodity_dict[key_commodity]]+text[0:5]+[' ']+text[-4:])
                            elif '-' in text:
                                pass
                            elif len(text) > 11: pass

                            else:
                                Extracted_text.append([Commodity_dict[key_commodity]]+text)
                        
                            text = []
                            if len(column_names)<11:
                                        column_names = ['Commodity', 'State Name', 'District Name', 'Market Name', 'Variety', 'Group', 
                                            'Arrivals (Tonnes)', 'Min Price (Rs./Quintal)', 'Max Price (Rs./Quintal)', 'Modal Price (Rs./Quintal)', 'Reported Date']
                        commodity_count.append([Commodity_dict[key_commodity]])
                        
                        if len(Extracted_text) > 545:
                            Extracted_text = []
                            for key in States_dict:
                                parameters = {'Tx_Commodity' : key_commodity,
                                            'Tx_State' : key,
                                            'Tx_District' : '0',
                                            'Tx_Market' : '0',
                                            'DateFrom' : DateFrom,
                                            'DateTo' : DateTo,
                                            'Fr_Date' : DateFrom,
                                            'To_Date' : DateTo,
                                            'Tx_Trend' : '2',
                                            'Tx_CommodityHead' : Commodity_dict[key_commodity],
                                            'Tx_StateHead' : '--Select--',
                                            'Tx_DistrictHead' : '--Select--',
                                            'Tx_MarketHead' : '--Select--'}
                                request_search = requests.get(url+'/SearchCmmMkt.aspx',params=parameters,timeout=30)
                                soup = BeautifulSoup(request_search.text,'html.parser')
                                column_names = []
                                for th_tags in soup.find_all('th'):
                                    b_tags = th_tags.find('b')
                                    column_names.append(str(b_tags.text).replace('<b>',''))
                                tr = soup.find_all('tr')[1:]
                                text = []
                                Extracted_text = []

                                for tr_tags in tr:
                                    for td_tags in tr_tags.find_all('td'):
                                        text.append(td_tags.text)
                                    if len(text) < 10:
                                        Extracted_text.append([Commodity_dict[key_commodity]]+text[0:5]+[' ']+text[-4:])
                                    elif '-' in text:
                                        pass
                                    elif len(text) > 11: pass

                                    else:
                                        Extracted_text.append([Commodity_dict[key_commodity]]+text)
                                
                                    text = []
                                    if len(column_names)<11:
                                        column_names = ['Commodity', 'State Name', 'District Name', 'Market Name', 'Variety', 'Group', 
                                            'Arrivals (Tonnes)', 'Min Price (Rs./Quintal)', 'Max Price (Rs./Quintal)', 'Modal Price (Rs./Quintal)', 'Reported Date']
                                    df = pd.DataFrame(Extracted_text,columns=column_names)
                                    Data_Extract_frames.append(df)
                                    
                        else:
                            df = pd.DataFrame(Extracted_text,columns=column_names)
                            Data_Extract_frames.append(df)
                    except Exception as e:
                        print(Extracted_text)
                        print(column_names)
                        print(f'Data Extract Failed for {Commodity_dict[key_commodity]} due to : {str(e)}')
                if len(Data_Extract_frames)>0:
                    data = pd.concat(Data_Extract_frames)
                    characters_to_remove = ['(', ')','/','']
                    pattern = '[' +  ''.join(characters_to_remove) +  ']'
                    characters_to_change = ['.',' ']
                    pattern_2 = '[' +  ''.join(characters_to_change) +  ']'
                    new_columns = []
                    for string in column_names:
                        string=re.sub(pattern,'',string)
                        string=re.sub(pattern_2,'_',string)
                        new_columns.append(string.upper())
                    zipped_object = zip(column_names,new_columns)
                    rename_dict  = {k:v for k,v in zipped_object}
                    data.rename(columns=rename_dict,inplace=True)
                    data.rename(columns={'GROUP':'COMMODITY_GROUP'},inplace=True)
                    UPLOAD_FLAG = None
                    METADATA = [[DateFrom,DateTo,data.shape[0],len(commodity_count),len(Commodity[1:]),len(States[1:])]]
                    COLUMN_NAMES_METADATA = ['FILE_DATE_FROM','FILE_DATE_TO','RECORDS_EXTRACTED','ENTRIES_RECORDED','COMMODITY_RECORDED','STATE_RECORDED']
                    metadata_frame = pd.DataFrame(METADATA,columns=COLUMN_NAMES_METADATA)
                    try:
                        data.to_csv(path + rf'\2023.csv', encoding='UTF-8', index=False)
                        UPLOAD_FLAG = True
                        # data.to_csv(path+rf'\ARGMARKET_{DateFrom}_TO_{DateTo}.csv',encoding='UTF-8')
                        # session.sql(f"select * from {session.get_current_database()}.{session.get_current_schema()}.{TABLE_NAME} limit 1").collect()
                        # session.write_pandas(df=data,table_name=TABLE_NAME,schema=session.get_current_schema(),quote_identifiers=False).collect()
                        # session.write_pandas(df=metadata_frame,table_name=METADATA_TABLE_NAME,schema=session.get_current_schema(),quote_identifiers=False).collect()
                        # UPLOAD_FLAG = True
                    except Exception as e:
                        print(f'Error saving CSV file: {str(e)}')
                        # session.write_pandas(df=data,table_name=TABLE_NAME,schema=session.get_current_schema(),auto_create_table=True,quote_identifiers=False).collect()
                        # session.write_pandas(df=metadata_frame,table_name=METADATA_TABLE_NAME,schema=session.get_current_schema(),quote_identifiers=False).collect()
                        # UPLOAD_FLAG = True
                        
                    if UPLOAD_FLAG:
                        print(f'''
                        Argmarket Extraction Complete the Following Stats :
                        1. Number of Comodity data Entried today : {len(commodity_count)}
                        2. Total Number of Rows Extracted : {data.shape[0]}
                        3. Total Number of Commodity Available : {len(Commodity[1:])} From {len(States[1:])} States
                        ''')
            except Exception as e:
                print(e)
        
        else:
            print(f'Site Returned Status Code {request.status_code}')
    except Exception as e:
        print(f'Site Not Responding : Error '+str(e))


In [5]:
from datetime import datetime
DateFrom = datetime(2023, 1, 1)
DateTo = datetime(2023, 12, 31)
Agmarknet_Extraction(DateFrom,DateTo,path)

  1%|█▏                                                                              | 5/345 [05:12<6:19:06, 66.90s/it]

[['Amaranthus', 'Kerala', 'Idukki', 'Adimali', 'Amaranthus', 'Vegetables', '0.04', '4000', '4000', '4000', '30 Dec 2023'], ['Amaranthus', 'Kerala', 'Idukki', 'Adimali', 'Amaranthus', 'Vegetables', '0.05', '4000', '4000', '4000', '29 Dec 2023'], ['Amaranthus', 'Kerala', 'Idukki', 'Adimali', 'Amaranthus', 'Vegetables', '0.06', '5000', '5000', '5000', '28 Dec 2023'], ['Amaranthus', 'Kerala', 'Idukki', 'Adimali', 'Amaranthus', 'Vegetables', '0.05', '4000', '4000', '4000', '27 Dec 2023'], ['Amaranthus', 'Kerala', 'Idukki', 'Adimali', 'Amaranthus', 'Vegetables', ' ', '4000', '4000', '4000', '26 Dec 2023'], ['Amaranthus', 'Kerala', 'Idukki', 'Adimali', 'Amaranthus', 'Vegetables', ' ', '4000', '4000', '4000', '23 Dec 2023'], ['Amaranthus', 'Kerala', 'Idukki', 'Adimali', 'Amaranthus', 'Vegetables', ' ', '4000', '4000', '4000', '22 Dec 2023'], ['Amaranthus', 'Kerala', 'Idukki', 'Adimali', 'Amaranthus', 'Vegetables', '0.04', '4000', '4000', '4000', '20 Dec 2023'], ['Amaranthus', 'Kerala', 'Idukki

  2%|█▊                                                                              | 8/345 [07:40<5:35:47, 59.78s/it]

[['Amphophalus', 'Kerala', 'Idukki', 'Adimali', 'Amphophalus', 'Cereals', '0.05', '5000', '6000', '5000', '30 Dec 2023'], ['Amphophalus', 'Kerala', 'Idukki', 'Adimali', 'Amphophalus', 'Cereals', ' ', '5000', '6000', '5000', '27 Dec 2023'], ['Amphophalus', 'Kerala', 'Idukki', 'Adimali', 'Amphophalus', 'Cereals', ' ', '6000', '6000', '6000', '26 Dec 2023'], ['Amphophalus', 'Kerala', 'Idukki', 'Adimali', 'Amphophalus', 'Cereals', '0.04', '5000', '6000', '5000', '23 Dec 2023'], ['Amphophalus', 'Kerala', 'Idukki', 'Adimali', 'Amphophalus', 'Cereals', '0.05', '5000', '6000', '5000', '22 Dec 2023'], ['Amphophalus', 'Kerala', 'Idukki', 'Adimali', 'Amphophalus', 'Cereals', ' ', '5000', '6800', '6000', '21 Dec 2023'], ['Amphophalus', 'Kerala', 'Idukki', 'Adimali', 'Amphophalus', 'Cereals', ' ', '5000', '6000', '6000', '20 Dec 2023'], ['Amphophalus', 'Kerala', 'Idukki', 'Adimali', 'Amphophalus', 'Cereals', ' ', '5000', '6000', '5000', '19 Dec 2023'], ['Amphophalus', 'Kerala', 'Idukki', 'Adimali',

  3%|██▌                                                                            | 11/345 [10:54<7:16:20, 78.38s/it]

...

100%|█████████████████████████████████████████████████████████████████████████████▊| 344/345 [5:49:37<00:33, 33.37s/it]

[['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', '0.10', '3000', '4000', '3500', '31 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', ' ', '3000', '4000', '3500', '29 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', '0.20', '3000', '4000', '3500', '28 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', '0.10', '3000', '4000', '3500', '27 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', ' ', '3000', '4000', '3500', '26 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', '0.20', '3000', '4000', '3500', '22 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', ' ', '3000', '4000', '3500', '21 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', '0.10', '3000', '4000', '3500', '20 Dec 2023'], ['WaterMelon', 'Himachal Pradesh

100%|██████████████████████████████████████████████████████████████████████████████| 345/345 [5:50:07<00:00, 60.89s/it]

[['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', '0.10', '3000', '4000', '3500', '31 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', ' ', '3000', '4000', '3500', '29 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', '0.20', '3000', '4000', '3500', '28 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', '0.10', '3000', '4000', '3500', '27 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', ' ', '3000', '4000', '3500', '26 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', '0.20', '3000', '4000', '3500', '22 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', ' ', '3000', '4000', '3500', '21 Dec 2023'], ['WaterMelon', 'Himachal Pradesh', 'Kullu', 'Bhuntar', 'Other', 'Fruits', '0.10', '3000', '4000', '3500', '20 Dec 2023'], ['WaterMelon', 'Himachal Pradesh


                        Argmarket Extraction Complete the Following Stats :
                        1. Number of Comodity data Entried today : 332
                        2. Total Number of Rows Extracted : 93965056
                        3. Total Number of Commodity Available : 345 From 36 States
                        
